In [36]:
import sys
import tweepy
import sys
import tweepy
from nltk.corpus import stopwords
import re
from collections import Counter
import pandas as pd
import unidecode
from nltk.stem import SnowballStemmer
from nltk.tokenize import RegexpTokenizer

consumer_key='S7e4bcPSpNhfHEeO64pjylwFC'
consumer_secret='cGLaCjvlDvfwqzkEn7hN3AkZlUMtrhLz7SFczsASnkexy10BBx'
access_key='959019738855862273-5rqxlIGK9aCvlo2z9JWahnFPcpfln2f'
access_secret='z2NQevSQfCdEp67FWYqnYd531J6KMCzp2zGjgESiP1JsX'

auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_key, access_secret)
api = tweepy.API(auth, wait_on_rate_limit=True)

# NLP
stemmer = SnowballStemmer('spanish')
tokenizer = RegexpTokenizer(r'\w+')
df = pd.read_csv('cities.csv', encoding='utf-8')

In [ ]:
auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_key, access_secret)
api = tweepy.API(auth)

def limit_handled(cursor):
    while True:
        try:
            yield cursor.next()
        except BaseException as e:
            print('failed_on_CURSOR_NEXT', str(e))
            time.sleep(5)
            global api
            api = tweepy.API(auth)
            yield cursor.next()

In [ ]:
df.head()

In [2]:
Andalusia = ["Andalusia", "37.3399964,-4.5811614,250km"]
#Extremadura = 
Madrid = ["Madrid", "40.5248319,-3.7715628,60km"]
Catalonia = ["Catalonia", "41.8523094,1.5745043,150km"]
#CastillaLaMancha = 
#CastillaLeon = 
#Cantabria = 
Basque_Country = ["Basque_Country", "42.9911816,-2.5543023,100km"]
#ComunidadValenciana = 
Canary_Islands = ["Canary_Islands", "28.5306525,-15.7464439,400km"]
#Aragon = 
#LaRioja = 
#Navarra = 
#Asturias = 
#Murcia = 

CAS = [Andalusia, Madrid, Catalonia, Basque_Country, Canary_Islands]

In [ ]:
#Rate limits are divided into 15 minute intervals. All endpoints require authentication, 
#so there is no concept of unauthenticated calls and rate limits. There are two initial buckets available 
#for GET requests: 15 calls every 15 minutes, and 180 calls every 15 minutes.

In [ ]:
list(df[df["admin"] == "Canary Islands"]["city"])

In [ ]:
CAS_ids = []
for CA in CAS:
    CA_cities = df[df["admin"] == CA[0]]["city"]
    tweets = tweepy.Cursor(api.search, geocode = CA[1]).items(300)  
    CA_ids = []
    for tweet in tweets:
        search_location = re.search('location\':(.+?),', str(tweet.user))
        if search_location:
            found_location = search_location.group(1)
            # Delete accent
            found_location = unidecode.unidecode(found_location)
            if any(word.lower() in found_location.lower() for word in CA_cities): 
                search_id = re.search('id\': (.+?),', str(tweet.user))
                if search_id:
                    found_id = search_id.group(1)
                    CA_ids.append(int(found_id))
                    print(found_id)
    CAS_ids.append(CA_ids)


In [ ]:
columns  =["Andalusia", "Madrid", "Catalonia", "Basque_Country", "Canary_Islands"]
df_ids = pd.DataFrame(data=list(zip(CAS_ids[0], CAS_ids[1], CAS_ids[2], CAS_ids[3], CAS_ids[4])),columns=columns)
print(df_ids)

In [ ]:
df_ids.to_csv("CAS_ids2.csv", index = False)

In [3]:
df_ids = pd.read_csv("CAS_ids.csv")

In [ ]:
df_ids.head()

In [37]:
def process_tweet(sentence):
    sentence = sentence.lower()
    sentence = unidecode.unidecode(sentence)
    words = tokenizer.tokenize(sentence)
    words = [w for w in words if not w in stopwords.words("spanish")]
    words = [w for w in words if (not "@" in w) if ("rt" != w.lower()) if (not "http" in w)]     # Delete words that contain mentions or the RT word 
    words = [stemmer.stem(w) for w in words] # Lemmatization spanish
    # Delete accent
    return words

In [6]:
# Now do for each CA
tweet_users_text = []
for CA in CAS:
    user_n = 1
    for user_id in df_ids[CA[0]]:
        tweet_n = 1
        user_id = int(user_id)
        user_id = str(user_id)
        try:      
            tweets = tweepy.Cursor(api.user_timeline, id=user_id).items(100)
            for tweet in tweets:
                tweet_text = [user_id, tweet.text, CA[0]]
                tweet_users_text.append(tweet_text)
                print("User {} of {} / Tweet {} of 100 in {}".format(user_n, len(df_ids[CA[0]]), tweet_n, CA[0]))
                tweet_n += 1
            user_n += 1
            
        except:
            "Ignore User"   

['3187391489', 'RT @Iyocnestospelos: Son las 9 de la mañana y ya estoy hasta los cojones del día', 'Andalusia']
User 1 of 104 / Tweet 1 of 100 in Andalusia
['3187391489', 'RT @mariaaaraamos: Soy la única que le tiene mucho miedo al futuro? eso de qué seremos, con quién estaremos, que pasará con las amistades,…', 'Andalusia']
User 1 of 104 / Tweet 2 of 100 in Andalusia
['3187391489', 'RT @realhorseguy: I can’t stop watching this specific TikTok https://t.co/3m7Vsksdvl', 'Andalusia']
User 1 of 104 / Tweet 3 of 100 in Andalusia
['3187391489', 'RT @juditvazzquez: Oye no dibujo bien pero quiero hacer este plan cn alguien o sea q guachi https://t.co/a0Vy0WUEPw', 'Andalusia']
User 1 of 104 / Tweet 4 of 100 in Andalusia
['3187391489', 'Punto y aparte', 'Andalusia']
User 1 of 104 / Tweet 5 of 100 in Andalusia
['3187391489', 'RT @KristyVicious: Dj no he preparado nada https://t.co/0fErXHmnDr', 'Andalusia']
User 1 of 104 / Tweet 6 of 100 in Andalusia
['3187391489', 'RT @akagoodgyal: Disculpa, ¿er

['3187391489', 'Eres una diva hermana https://t.co/2bKbgODVry', 'Andalusia']
User 1 of 104 / Tweet 61 of 100 in Andalusia
['3187391489', 'RT @irenetrujis: Instagram ahora parece un karaoke', 'Andalusia']
User 1 of 104 / Tweet 62 of 100 in Andalusia
['3187391489', 'Lo haces en las playas d grana y lo mismo no te tienen q poner puntos https://t.co/3TVZsWrgzu', 'Andalusia']
User 1 of 104 / Tweet 63 of 100 in Andalusia
['3187391489', 'RT @manu10fuster: en mi casa me enseñaron que si yo tengo 10€ y mi amigo 0€ los dos tenemos 5€', 'Andalusia']
User 1 of 104 / Tweet 64 of 100 in Andalusia
['3187391489', 'RT @maricelimcc: Real que me aburro lo más grande y no sé que hacer hoy', 'Andalusia']
User 1 of 104 / Tweet 65 of 100 in Andalusia
['3187391489', 'RT @Valopezv: Me da miedo el concepto de “gordura” que tiene la sociedad hoy en día https://t.co/LdlqxCPbep', 'Andalusia']
User 1 of 104 / Tweet 66 of 100 in Andalusia
['3187391489', 'RT @Nuriaperez26: estamos todos de acuerdo en que esta es la m

['284794206', '@kitohhhh Si me toca te regalo un viaje a Gorgonia que seguro que la echas de menos 👌🏼', 'Andalusia']
User 2 of 104 / Tweet 21 of 100 in Andalusia
['284794206', '@telemgzn @fertejerom @vanesa_romero @MirenIbarguren @evaisantaf @LQSAtelecinco @LQSAInformacion @MontepinarTodo… https://t.co/oqoPYUPuhL', 'Andalusia']
User 2 of 104 / Tweet 22 of 100 in Andalusia
['284794206', '@assassinsspain Fallos del juego al usar el teletransporte del Elíseo. Cierra la aplicación. Y para colmo una de la… https://t.co/TXNav17zpR', 'Andalusia']
User 2 of 104 / Tweet 23 of 100 in Andalusia
['284794206', '@LaResistencia Y cuando al final le señala con la mano por donde tiene que irse y le dice "por allí"?', 'Andalusia']
User 2 of 104 / Tweet 24 of 100 in Andalusia
['284794206', '@navedelmisterio @ferranbarber Es que como no son cristianos blancos ni es en Europa o América no pasa nada...', 'Andalusia']
User 2 of 104 / Tweet 25 of 100 in Andalusia
['284794206', '@hobby_consolas Os silencio has

['284794206', '@PSPlusES @PlayStationES A @hermanntertsch claramente. Eso sí, tiene que haber cócteles del barman de… https://t.co/6Q5lEOGy8C', 'Andalusia']
User 2 of 104 / Tweet 81 of 100 in Andalusia
['284794206', '@assassinsspain @MarinaBraBra Podríais dar la autorización a @VideojuegosGAME para que ponga ya el Odisea en venta… https://t.co/W4vybsAkDN', 'Andalusia']
User 2 of 104 / Tweet 82 of 100 in Andalusia
['284794206', '@guardiacivil O por resolver crímenes como los del caso Quer y del pequeño Gabriel... Ah pero como eso no es una cr… https://t.co/rmEu0WGsWg', 'Andalusia']
User 2 of 104 / Tweet 83 of 100 in Andalusia
['284794206', '@LaResistencia Si escribes en castellano lo correcto es poner Cataluña. Al igual que has escrito Japón y no 日本 en mi humilde opinión.', 'Andalusia']
User 2 of 104 / Tweet 84 of 100 in Andalusia
['284794206', 'RT @Rubiu5: LIMONADA 2.0 🗿', 'Andalusia']
User 2 of 104 / Tweet 85 of 100 in Andalusia
['284794206', '@EiProfeta Cuando decís en voz alta Hermi

['475728390', 'RT @iree_rme: Estoy entre el "venga último empujón" y el "a tomar por culo a ver si me muero"', 'Andalusia']
User 3 of 104 / Tweet 41 of 100 in Andalusia
['475728390', 'RT @Resiliencee_: Tu coche es alemán. El vodka que bebes es ruso, la pizza de Italia, el kebab turco.Tu democracia nació en Grecia. Tu café…', 'Andalusia']
User 3 of 104 / Tweet 42 of 100 in Andalusia
['475728390', 'Totalmente de acuerdo🙋🏽🙂 https://t.co/JEDYp2Xf9b', 'Andalusia']
User 3 of 104 / Tweet 43 of 100 in Andalusia
['475728390', 'RT @RguezzAle: antes d ti no sabía lo que era mirar a alguien y tener miedo d perderle', 'Andalusia']
User 3 of 104 / Tweet 44 of 100 in Andalusia
['475728390', 'RT @thxhannibal: ·.༄࿔ Sᴏʟᴏ ᴍᴜᴇʀᴇ ϙᴜɪᴇɴ ᴇs ᴏʟᴠɪᴅᴀᴅo ʏ ᴀ ᴍɪ ᴍᴇ ᴠᴀɴ ᴀ ʀᴇᴄᴏʀᴅᴀʀ.\n \n»Cʀᴜᴢ ᴅᴇʟ suʀ / norte\n»ᴀsᴇsɪɴᴀᴛᴏ. ᴛᴇɴᴇɴᴄɪᴀ ɪʟɪ́ᴄɪᴛᴀ. ʀᴏʙo\n»P…', 'Andalusia']
User 3 of 104 / Tweet 45 of 100 in Andalusia
['475728390', 'RT @joseluuu8: fav si eres de esos valientes que vas por la vida con la ropa llena de pelo de 

...

['770582588', '@laurisMel_  no es consciente de que hoy le toca un día de compras conmigo', 'Canary_Islands']
User 46 of 104 / Tweet 21 of 100 in Canary_Islands
['770582588', 'Graacias cariño🖤\U0001f970 https://t.co/cfC7zYVhSK', 'Canary_Islands']
User 46 of 104 / Tweet 22 of 100 in Canary_Islands
['770582588', 'Chiquis que las aprobé todas 😭', 'Canary_Islands']
User 46 of 104 / Tweet 23 of 100 in Canary_Islands
['770582588', 'Digo, un poco de educación https://t.co/zUCl4J01rR', 'Canary_Islands']
User 46 of 104 / Tweet 24 of 100 in Canary_Islands
['770582588', '@fabiolasocas Y un verano quedando un día conmigo?', 'Canary_Islands']
User 46 of 104 / Tweet 25 of 100 in Canary_Islands
['770582588', '@Nub3in3rt3 Ni me los nombres \U0001f92c', 'Canary_Islands']
User 46 of 104 / Tweet 26 of 100 in Canary_Islands
['770582588', 'Me da la sensación que mi profesora me aprobó el examen porque pensó que no daba más de mi después de leer toda la mierda que puse.', 'Canary_Islands']
User 46 of 104 / 

['770582588', '2:15 mi novia y yo hablando en inglés con la luz oscura', 'Canary_Islands']
User 46 of 104 / Tweet 81 of 100 in Canary_Islands
['770582588', 'RT @FranPardo_: Hablar de #OrgulloLGTBI es hablar de Stonewall Inn, lugar en el q el 28 de junio de 1969 se iniciaron las revueltas de #Sto…', 'Canary_Islands']
User 46 of 104 / Tweet 82 of 100 in Canary_Islands
['770582588', 'Saben qué es peor que trabajar un sábado? Estudiar en el trabajo un sábado', 'Canary_Islands']
User 46 of 104 / Tweet 83 of 100 in Canary_Islands
['770582588', 'Cuando estas estudiando y no te entra nada https://t.co/Hri5ec4wh0', 'Canary_Islands']
User 46 of 104 / Tweet 84 of 100 in Canary_Islands
['770582588', 'RT @giulibonino1: Ustedes también se olvidan de que tienen tatuajes? Porque yo si', 'Canary_Islands']
User 46 of 104 / Tweet 85 of 100 in Canary_Islands
['770582588', 'Estrés, drama y drogas. \nMe falta una y no son las dos primeras. https://t.co/PFsUPbiERF', 'Canary_Islands']
User 46 of 104 / Tweet 8

['3372209741', 'RT @MiPatanFavorito: mira abajo\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.\n.…', 'Canary_Islands']
User 47 of 104 / Tweet 41 of 100 in Canary_Islands
['3372209741', 'RT @frangxrcia: si piensas "rabia" dice rabia y si piensas "rollo" dice rollo https://t.co/cATZCmkCFa', 'Canary_Islands']
User 47 of 104 / Tweet 42 of 100 in Canary_Islands
['3372209741', 'RT @morocha_fem: Esta es la mariposa de la buena suerte, cuenta la leyenda que si no le das rt te irá mal en todos los exámenes. https://t.…', 'Canary_Islands']
User 47 of 104 / Tweet 43 of 100 in Canary_Islands
['3372209741', 'RT @SeergioCabellos: nadie: \n\nmi mente: me llamo maria jose me gustan los libros, soy taciturna...  vegetariana... animalista\n\nyo: \n\nhttps:…', 'Canary_Islands']
User 47 of 104 / Tweet 44 of 100 in Canary_Islands
['3372209741', 'RT @_marcelaprado: El video de María José completo 

['3372209741', 'RT @pablomllnprz: Alguien: Eres un dramático.\nYo: \nhttps://t.co/twjMfFCvqy', 'Canary_Islands']
User 47 of 104 / Tweet 99 of 100 in Canary_Islands
['3372209741', 'RT @javitm99: La hostia de los exámenes de mayo https://t.co/YqnazefmjW', 'Canary_Islands']
User 47 of 104 / Tweet 100 of 100 in Canary_Islands
['2932170106', 'RT @estebansevillaa: Mi reacción cuando escuché el intro de "Otro Trago Remix” 🤣🔥 https://t.co/9I5KjsA6ZH', 'Canary_Islands']
User 48 of 104 / Tweet 1 of 100 in Canary_Islands
['2932170106', 'RT @solilluna_: Oye no echáis de menos las excursiones del colegio. En plan despertarte un día y estar contento porque ni tenías clase y te…', 'Canary_Islands']
User 48 of 104 / Tweet 2 of 100 in Canary_Islands
['2932170106', 'RT @sandracula_: nada se siente tanto como las partes de las canciones que son indirectas hacia otra persona y las cantas a grito pelao', 'Canary_Islands']
User 48 of 104 / Tweet 3 of 100 in Canary_Islands
['2932170106', 'Chiquita depresión 

['2932170106', 'RT @pepeviyuelacf: rúlate la rutina de fijación del meikap amiga https://t.co/uFJDni6V1V', 'Canary_Islands']
User 48 of 104 / Tweet 59 of 100 in Canary_Islands
['2932170106', 'RT @melmuertos: se ha hecho viral un vídeo en el q salgo gritando te quiero borracha 🤠 https://t.co/iGnOBbRPgt', 'Canary_Islands']
User 48 of 104 / Tweet 60 of 100 in Canary_Islands
['2932170106', 'RT @lenagoomi: T meto un cabezazo q no t lo crees https://t.co/yMs4KEzmAu', 'Canary_Islands']
User 48 of 104 / Tweet 61 of 100 in Canary_Islands
['2932170106', 'RT @andresitococaaa: Mangando los hielos en el botellón https://t.co/WmU7Ft6l4B', 'Canary_Islands']
User 48 of 104 / Tweet 62 of 100 in Canary_Islands
['2932170106', 'RT @lakiwi_xx: Que no se puede hacer humor sin ofender decían y aquí estoy despollandome viva https://t.co/EAVFxKClpt', 'Canary_Islands']
User 48 of 104 / Tweet 63 of 100 in Canary_Islands
['2932170106', 'Con la inseguridad que tengo, si lo hago yo, seguro que molesta\U0001f974 htt

In [13]:
df_tweets = pd.DataFrame(tweet_users_text, columns = ["id", "tweet", "location"])

In [14]:
df_tweets.to_csv("tweet_dataset.csv", encoding='utf-8-sig', index = False)

In [19]:
count_CA = Counter(list(df_tweets["location"])).most_common(5)
print(new_vals)

In [39]:
for CA in CAS:
    group_words = []
    for index, row in df_tweets[df_tweets["location"] == CA[0]].iterrows():
        words = process_tweet(row[1])
        group_words += words
    count_words = Counter(group_words).most_common(10)
    print("\nFor {}:".format(CA[0]))
    print(count_words)


For Andalusia:
[('t', 3280), ('co', 3219), ('si', 564), ('mas', 412), ('0', 378), ('hac', 330), ('pas', 238), ('q', 229), ('quier', 228), ('pued', 221)]

For Madrid:
[('t', 3182), ('co', 3120), ('mas', 471), ('si', 432), ('hac', 280), ('pued', 197), ('ser', 187), ('quier', 186), ('the', 172), ('pas', 158)]

For Catalonia:
[('t', 1430), ('co', 1377), ('i', 226), ('the', 215), ('si', 177), ('l', 176), ('mas', 133), ('d', 131), ('to', 123), ('and', 112)]

For Basque_Country:
[('t', 3279), ('co', 3228), ('si', 456), ('mas', 450), ('hac', 293), ('pas', 196), ('pued', 182), ('quier', 172), ('ver', 156), ('ser', 151)]

For Canary_Islands:
[('t', 2478), ('co', 2422), ('si', 347), ('mas', 317), ('eldi', 216), ('hac', 203), ('canari', 166), ('cdaxii', 158), ('quier', 141), ('pas', 138)]


In [ ]:
# We see that most of the words are similar for each CA
# What will have more weight in the classification will be the words for cities mentioned in the tweets
# also the expressions typical of each place